Find an algorithm for cycle decomposition of an abritrary permutation.

In [89]:
import Pkg; 
Pkg.add("AbstractAlgebra")
Pkg.add("JackPolynomials")
Pkg.add("Permutations")
Pkg.add("NumericalRepresentationTheory")

   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`
   Resolving package versions...
  No Changes to `~/.julia/environments/v1.7/Project.toml`
  No Changes to `~/.julia/environments/v1.7/Manifest.toml`


In [90]:
#Pkg.add("Combinatorics")
#using Combinatorics

In [91]:
using LinearAlgebra, AbstractAlgebra, Permutations, JackPolynomials, NumericalRepresentationTheory

[ Info: Precompiling NumericalRepresentationTheory [6b7c1d51-ecee-4149-97a8-50646b514dce]
┌ Warning: Module Permutations with build ID 10265887817842875 is missing from the cache.
│ This may mean Permutations [2ae35dd2-176d-5d53-8349-f30d82d94d4f] does not support precompilation but is imported by a module that does.
└ @ Base loading.jl:1107
[ Info: Skipping precompilation since __precompile__(false). Importing NumericalRepresentationTheory [6b7c1d51-ecee-4149-97a8-50646b514dce].
[ Info: Precompiling Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80]
┌ Warning: Module JSON with build ID 7159489459114250 is missing from the cache.
│ This may mean JSON [682c06a0-de6a-54ab-a142-c8b1cf79cde6] does not support precompilation but is imported by a module that does.
└ @ Base loading.jl:1107
[ Info: Skipping precompilation since __precompile__(false). Importing Plots [91a5bcdd-55d7-5caf-9e0b-520d859cae80].


LoadError: LoadError: UndefVarError: AbstractPermutation not defined
in expression starting at /Users/jkunes/.julia/packages/NumericalRepresentationTheory/tXpmI/src/NumericalRepresentationTheory.jl:1

In [92]:
a=[1,2,5,3,4]
ap = Permutation(a)
b = [2,3,5,4,1]
bp = Permutation(b)

(1,2,3,5)(4)

We want to study $T_{2g}$ states in the point group O. Our goal is to find the irreps for configurations of $t^2$, $t^3$ and $t^4$ and $t^5$, i.e. we want to find irreps. of O in $T_{2g}\otimes T_{2g}\otimes T_{2g}\otimes\ldots$. We need more that just characters of $T_{2g}$. We need the eigenvalues $\lambda_i(g)$. Note that $\chi(g)=\sum_i\lambda_i$ and that the set $\{\lambda_i(g)\}$ is a class function.

Here we generate the eigenvalues of $T_{2g}$ representation for each class. Note, that like character also the set of eigenvalues is a class functions, i.e., it is enough to the eigenvalues for one operation from the class. Do not worry about how the number are generated (for some I put in the matrix $D(g)$, others are so simple that I put in the eigenvalues directly).

In [95]:
lambda=Vector{Vector}()
#"E"
push!(lambda,[1,1,1])
#"C3"
push!(lambda,eigvals([0 1 0; 0 0 1; 1 0 0]))
#"C2"
push!(lambda,eigvals([1 0 0; 0 0 -1; 0 -1 0]))
#"C4"
push!(lambda,eigvals([-1 0 0; 0 0 -1; 0 1 0]))
#"C2"
push!(lambda,[1,-1,-1])

5-element Vector{Vector}:
 [1, 1, 1]
 ComplexF64[-0.5 - 0.8660254037844389im, -0.5 + 0.8660254037844389im, 0.9999999999999998 + 0.0im]
 [-1.0, 1.0, 1.0]
 ComplexF64[-1.0 + 0.0im, 0.0 - 1.0im, 0.0 + 1.0im]
 [1, -1, -1]

We will also look at the full $d$ shell. We use that $\Gamma_{l=2}=T_{2g}\oplus E_g$ and so we also need the eigenvalkues for the $E_g$ representation, which we get below.

In [96]:
lambda2=Vector{Vector}()
#"E"
push!(lambda2,[1,1])
#"C3"
push!(lambda2,eigvals([-1/2 -sqrt(3)/2; sqrt(3)/2 -1/2]))
#"C2"
push!(lambda2,[-1,1])
#"C4"
push!(lambda2,[-1, 1])
#"C2"
push!(lambda2,[1,1])

5-element Vector{Vector}:
 [1, 1]
 ComplexF64[-0.5 - 0.8660254037844386im, -0.5 + 0.8660254037844386im]
 [-1, 1]
 [-1, 1]
 [1, 1]

We are going to use the Schur-Weyl duality $V^{n\otimes}=\bigoplus_{\lambda} V_\lambda \otimes S_\lambda$, where $V_\lambda$ is a representation of O and $S_\lambda$ a representation of $S_n$. Our goal is to find the characters of $V_\lambda$ and decompose them to irreps.

First, we look at the special case of symmetric representation. Here the character can be calcualated using $\chi(g)=\sum_{n_1+n_2+n_3=n}\lambda_1(g)^{n_1}\lambda_2(g)^{n_2}\lambda_2(g)^{n_2}$. This formula is derived in SymProd notebook.
The below functions evaluate a single contribution for given partition, generate all partitions and sum over all partitions. (We will not use this function later, instead we will implement calculation of $\chi(g)$ for arbitrary Young diagram.)

In [99]:
function chi(lambda::Vector, distributions::Vector{Vector{Int}})
    out = 0.
    for x in distributions
        s = 1
        for i in eachindex(lambda)
            s *=lambda[i]^x[i]
        end
        out +=s
    end
    return out
end


chi (generic function with 1 method)

In [159]:
# This is an explicit implementation of code to partition an integer N as a sum of m non-negative integeres. Later we will use a function provided by one of the used libraries. 

function decompose_integer(N::Int, m::Int)::Vector{Vector{Int}}
    result = Vector{Vector{Int}}()
    partition_helper!(result, Int[], N, m)
    return result
end

function partition_helper!(result::Vector{Vector{Int}}, current::Vector{Int}, remaining::Int, m::Int)
    if m == 0
        if remaining == 0
            push!(result, copy(current))  # Store a valid partition
        end
        return
    end
    for i in 0:remaining
        push!(current, i)
        partition_helper!(result, current, remaining - i, m - 1)
        pop!(current)  # Backtrack
    end
end

partition_helper! (generic function with 1 method)

In [161]:
decompose_integer(5,3)

21-element Vector{Vector{Int64}}:
 [0, 0, 5]
 [0, 1, 4]
 [0, 2, 3]
 [0, 3, 2]
 [0, 4, 1]
 [0, 5, 0]
 [1, 0, 4]
 [1, 1, 3]
 [1, 2, 2]
 [1, 3, 1]
 [1, 4, 0]
 [2, 0, 3]
 [2, 1, 2]
 [2, 2, 1]
 [2, 3, 0]
 [3, 0, 2]
 [3, 1, 1]
 [3, 2, 0]
 [4, 0, 1]
 [4, 1, 0]
 [5, 0, 0]

In [163]:
# Generates the characted of operation g (specified by eigenvalues lambda) in symmetric (trivial) representation.

function sym_chi(lambda::Vector, n::Int)
    out = Vector()
    dim = length(lambda[1])
    part = decompose_integer(n, dim)
    for g in lambda
        x = round(Int, real(chi(g,part)))
        push!(out,x)
    end
    return out
end


sym_chi (generic function with 1 method)

Similar as the above, but for abitrary representations of $S_n$ specified by the Young Tableau. It takes
the eigenvalues $\lambda_i$ of $D(g)$ and the Young Tableau (part) as an input.

In [103]:
function chi_lambda(lambda::Vector, part::Vector{Int})
    out = Vector()
    for g in lambda
        x = round(Int,real(JackPolynomials.Schur(g,part)))
        push!(out,x)
    end
    return out
end

chi_lambda (generic function with 1 method)

The same as above, but loops over all Young Tableax of $S_n$.

In [207]:
function chiVn(lambda::Vector, n::Int)
    out = Vector()
    parts = Generic.partitions(n)
    for part in parts
#        println(collect(part))
        chi = chi_lambda(lambda, collect(part))
        push!(out,chi)
    end
    return parts,out
end
    

chiVn (generic function with 1 method)

In [106]:
parts,char = chiVn(lambda,3);
for i in eachindex(parts)
    println(parts[i],"    ",map(x->round(Int,x),char[i]), "  x   ",character(parts[i],parts[1]))
end

[1, 1, 1]
[2, 1]
[3]
1₃    [1, 1, -1, -1, 1]  x   1
2₁1₁    [8, -1, 0, 0, 0]  x   2
3₁    [10, 1, 2, 0, -2]  x   1


In [169]:
parts2,char2 = chiVn(lambda2,2);
for i in eachindex(parts2)
    println(parts2[i],"    ",map(x->round(Int,x),char2[i]), "  x   ",character(parts2[i],parts2[1]))
end

[1, 1]
[2]
1₂    [1, 1, -1, -1, 1]  x   1
2₁    [3, 0, 1, 1, 3]  x   1


In [171]:
YoungTableau(parts[4])

┌───┬───┐
│ 1 │ 2 │
├───┼───┤
│ 3 │ 4 │
├───┼───┘
│ 5 │
└───┘

Compututes the character table of the group $S_n$. Both the classes and the irreps are labeled by Young Tableaux.

In [110]:
n = length(parts)
Ctable = zeros(Int,n,n)
for i in 1:n
    for j in 1:n
        Ctable[i,j]=character(parts[i],parts[j])
    end
end

Ctable

3×3 Matrix{Int64}:
 1  -1   1
 2   0  -1
 1   1   1

In [111]:
# Function to compute the number of elements in the conjugacy class of a partition of n
function conjugacy_class_size(n::Int, partition::Vector{Int})
    # Step 1: Compute n!
    total_factorial = factorial(n)

    # Step 2: Compute the product of (n_i^{m_i} * m_i!) for each part n_i in the partition
    denom = 1
    unique_parts = unique(partition)  # The distinct parts in the partition
    for part in unique_parts
        m_i = count(x -> x == part, partition)  # Count how many times part appears in the partition
        denom *= (part^m_i) * factorial(m_i)  # Compute the denominator for this part
    end

    # Step 3: Return the size of the conjugacy class
    return total_factorial ÷ denom
end

# Example usage:
n = 5
partition = [3, 1, 1]  # This corresponds to a partition (3,1,1) of n=5
println("Number of elements in the conjugacy class: ", conjugacy_class_size(n, partition))

Number of elements in the conjugacy class: 20


In [112]:
function zrho(n::Int)
    parts = Generic.partitions(n)
    l = length(parts)
    out = [ conjugacy_class_size(n, parts[i].part) for i in 1:l]
end

zrho (generic function with 1 method)

Calculates the (Clebsch-Gordan) decompositions $\Gamma_a\otimes \Gamma_b = {\Large \oplus}_i a_i \Gamma_i$, where 
$a_i = \frac{1}{n!}\sum_{C \in \text{classes of S}_n} N_C\Gamma_i(C)\Gamma_a(C)\Gamma_g(C)$. Prints the full set of $a_i$ including zeros.

In [113]:
function Kronecker(n::Int64, a::AbstractAlgebra.Generic.Partition{Int64}, b::AbstractAlgebra.Generic.Partition{Int64})
    out = Vector()
    parts = Generic.partitions(n)
    l = length(parts)
    fac = zrho(n)/factorial(n)
    for i in 1:l
        sum = 0
        for j in 1:l
            sum += character(a,parts[j]).*character(b,parts[j])*character(parts[i],parts[j])*fac[j]
        end
        push!(out,sum)
    end
    return out
end
        


Kronecker (generic function with 1 method)

In [205]:
# Test of Kronecker
x=round.(Int,Kronecker(5, parts[1],parts[2]))
print(x)
div = parts[findfirst(==(1), x)].part
if length(div)==2 
    S = (div[1]-div[2])/2
end


[0, 0, 0, 0, 1, 0, 0]

1.5

In [199]:
# Function to format a Partition or YoungTableau into a readable string chatGPT generated
function format_gamma(gamma)
    return string(gamma)
end

# Function to print the equation in the desired format with only non-zero coefficients
function print_equation(a::String, b::String, gammas::Vector{AbstractAlgebra.Generic.Partition{Int64}}, coefs::Vector{Int})
    # Create the equation string
    equation = "$a ⊗ $b = "
    
    terms = []

    for (coef, gamma) in zip(coefs, gammas)
        if coef != 0  # Only include terms with non-zero coefficients
            term = "$coef $(format_gamma(gamma))"
            push!(terms, term)
        end
    end
    
    # If terms are not empty, join them with ' ⊕ ' and print the final equation
    if length(terms) > 0
        println(equation * join(terms, " ⊕ "))
    else
        println(equation * "0")  # If no non-zero terms, print 0
    end
end

# Example usage:
gamma1 = Partition([3, 2, 1])  # Define a Partition
gamma2 = Partition([2, 2])     # Define another Partition
n1 = 2                         # Coefficient for gamma1
n2 = 0                         # Coefficient for gamma2 (zero coefficient, won't be included)
n3 = 3                         # Coefficient for another gamma3 (to be added later)
gamma3 = Partition

Partition (generic function with 2 methods)

In [203]:
# test of Kronecker and printing
i=2
j=4
coefs = round.(Int, Kronecker(5,parts[i],parts[j]))
print_equation("A","B",parts, coefs)

A ⊗ B = 1 3₁1₂ ⊕ 1 2₂1₁ ⊕ 1 4₁1₁ ⊕ 1 3₁2₁


Collect the eigenvalues for each $O$ class for the full $d$-shell: $\Gamma_{l=2}=E\oplus T_2$.

In [118]:
tot = Vector()
for i in eachindex(lambda2)
    push!(tot,vcat(lambda2[i],lambda[i]))
end
tot

5-element Vector{Any}:
 [1, 1, 1, 1, 1]
 ComplexF64[-0.5 - 0.8660254037844386im, -0.5 + 0.8660254037844386im, -0.5 - 0.8660254037844389im, -0.5 + 0.8660254037844389im, 0.9999999999999998 + 0.0im]
 [-1.0, 1.0, -1.0, 1.0, 1.0]
 ComplexF64[-1.0 + 0.0im, 1.0 + 0.0im, -1.0 + 0.0im, 0.0 - 1.0im, 0.0 + 1.0im]
 [1, 1, 1, -1, -1]

Compute the orbital decomposition $V^{n\otimes}=\bigoplus_{\lambda} V_\lambda \otimes S_\lambda$. The same decomposition exists for the spin part. The total "orbital x spin" wave fucntion must be antisymmetric (irrep #1). In principle we should combine ($\otimes$) all YTs for orbital part with all YTs for spin part decompose into irreps and find if and how many times (function Kronecker) #1 is in contained. However, note that the Kronecker formula is symmetric. Therefore, if I have an irrep $\Gamma_m$ I want to know which irreps I have to multiply it with to get $\Gamma_1$ it is the same as asking for decomposition of $\Gamma_m\otimes\Gamma_1$. It turns out that 
$\Gamma_m\otimes\Gamma_1=\overline{\Gamma_m}$, which is just a trasnposed YT. Not every YT can be represented on the basis of spin functions.
Since the spin has only two possible values only YTs with maximum two rows are compatible with a spin wavefunction, i.e. a partion
$(N_\uparrow,N_\downarrow)$ corresponding to $S=\tfrac{N_\uparrow-N_\downarrow}{2}$. 

On the output one gets the characters of the orbital part of the representation of $O$ group. These can be used with the online tool to find the decompositions into irreps. This is the main results and allow one to get the terms in the cubic crystal field of the type
$^{2S+1}T_{1g}$. Note, that the orbital and spin part restrict each other. This restriction is the consequence of the Pauli principle, which requires that the total wave function transforms as totally anti-symmetric representation of $S_n$.

In [209]:
n=5
parts,char = chiVn(tot,n);
for i in eachindex(parts)
    out = false
    x=round.(Int,Kronecker(n, parts[1],parts[i]))
    div = parts[findfirst(==(1), x)].part
    if length(div)==1 
        out = true
        S = div[1]/2    
    elseif length(div)==2 
        out = true
        S = (div[1]-div[2])/2
    end
    if out
        println(parts[i],"    ",map(x->round(Int,x),char[i]), "  x  S=", S)
    else
        println(parts[i],"    ",map(x->round(Int,x),char[i]), "  X   ")
    end
end

1₅    [1, 1, 1, 1, 1]  x  S=2.5
2₁1₃    [24, 0, 0, 0, 0]  x  S=1.5
3₁1₂    [126, 0, -6, 0, -6]  X   
2₂1₁    [75, 0, 3, -1, 3]  x  S=0.5
4₁1₁    [224, 2, 0, 0, 0]  X   
3₁2₁    [175, -2, 3, 1, 3]  X   
5₁    [126, 0, 6, -2, 6]  X   


In [121]:
lambda2

5-element Vector{Vector}:
 [1, 1]
 ComplexF64[-0.5 - 0.8660254037844386im, -0.5 + 0.8660254037844386im]
 [-1, 1]
 [-1, 1]
 [1, 1]